# HW 2 - Question 1: Titanic Data Set 

## Data preprocessing

### Load the libraries

In [92]:
# Python ≥3.5 is required
import sys
assert sys.version_info >= (3, 5)

# Scikit-Learn ≥0.20 is required
import sklearn
assert sklearn.__version__ >= "0.20"

# Common imports
import numpy as np
import pandas as pd
import os
import random as rnd

## ML libraries

from sklearn.datasets import load_iris

from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC, LinearSVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import Perceptron
from sklearn.linear_model import SGDClassifier
from sklearn.tree import DecisionTreeClassifier

from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn import metrics

# visualization
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

# to make this notebook's output stable across runs
np.random.seed(42)

### Load the data 

In [4]:
trainpath='./train.csv'

testpath='./test.csv'


df_trn=pd.read_csv(trainpath)
df_trn.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [5]:
df_tst=pd.read_csv(testpath)

df_tst.head()

PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  34.5      0      0   330911   7.8292   NaN        Q  
1  47.0      1      0   363272   7.0000   NaN        S  
2  62.0      0      0   240276   9.6875   NaN        Q  
3  27.0      0      0   315154   8.6625   NaN        S  
4  22.0      1      1  3101298  12.2875   NaN        S

In [29]:
combine = [df_trn,df_tst]

### first look into the data 

In [31]:
for data in combine:
    print('_'*50)
    print(data.describe())
    print('_'*50)


__________________________________________________
       PassengerId    Survived      Pclass         Age       SibSp  \
count   891.000000  891.000000  891.000000  714.000000  891.000000   
mean    446.000000    0.383838    2.308642   29.699118    0.523008   
std     257.353842    0.486592    0.836071   14.526497    1.102743   
min       1.000000    0.000000    1.000000    0.420000    0.000000   
25%     223.500000    0.000000    2.000000   20.125000    0.000000   
50%     446.000000    0.000000    3.000000   28.000000    0.000000   
75%     668.500000    1.000000    3.000000   38.000000    1.000000   
max     891.000000    1.000000    3.000000   80.000000    8.000000   

            Parch        Fare  
count  891.000000  891.000000  
mean     0.381594   32.204208  
std      0.806057   49.693429  
min      0.000000    0.000000  
25%      0.000000    7.910400  
50%      0.000000   14.454200  
75%      0.000000   31.000000  
max      6.000000  512.329200  
______________________________

In [43]:
for data in combine:
    print("-"*40)
    print(data.describe(include=['O']))
df_trn.describe(include=['O'])

----------------------------------------
                                     Name   Sex Ticket    Cabin Embarked
count                                 891   891    891      204      889
unique                                891     2    681      147        3
top     Pears, Mrs. Thomas (Edith Wearne)  male   1601  B96 B98        S
freq                                    1   577      7        4      644
----------------------------------------
                                  Name   Sex    Ticket            Cabin  \
count                              418   418       418               91   
unique                             418     2       363               76   
top     Baimbrigge, Mr. Charles Robert  male  PC 17608  B57 B59 B63 B66   
freq                                 1   266         5                3   

       Embarked  
count       418  
unique        3  
top           S  
freq        270  


Name   Sex Ticket    Cabin Embarked
count                                 891   891    891      204      889
unique                                891     2    681      147        3
top     Pears, Mrs. Thomas (Edith Wearne)  male   1601  B96 B98        S
freq                                    1   577      7        4      644

In [33]:
print(df_trn.columns.values)

['PassengerId' 'Survived' 'Pclass' 'Name' 'Sex' 'Age' 'SibSp' 'Parch'
 'Ticket' 'Fare' 'Cabin' 'Embarked']


### Feature Identification

Numerical features:  'Age' 'SibSp' 'Parch' 'Fare' 
 
Catagorical:  'PassengerId' 'Survived' 'Pclass' 'Name' 'Sex' 'Ticket'  'Cabin' 'Embarked'



In [34]:
# df_trn.isnull().sum()
for data in combine:
    print("="*40)
    print(data.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB
None
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pcl

In [12]:
df_tst_cat["Embarked"]=df_tst_cat["Embarked"].replace(to_replace=['C','Q','S'],value=[1,2,3])

In [ ]:

df.Sex = df['Sex'].replace(to_replace ="male", value = 0)
df.Sex = df['Sex'].replace(to_replace ="female", value = 1)
df['Embarked'].fillna('S', inplace=True)
df_tst_cat["Embarked"]=df_tst_cat["Embarked"].replace(to_replace=['C','Q','S'],value=[1,2,3])

In [50]:
## Feature Selection Dropping ticket passenger and cabin

# not relevant to us

In [46]:
for d in combine:
    d=d.drop(['Ticket','PassengerId','Cabin'],1)

In [52]:
df_trn=df_trn.drop(['Ticket','PassengerId','Cabin'],1)
df_tst=df_tst.drop(['Ticket','PassengerId','Cabin'],1)
combine = [df_trn,df_tst]

In [54]:
for dataset in combine:
    dataset['Title'] = dataset.Name.str.extract(' ([A-Za-z]+)\.', expand=False) ## extract the first of the name
    dataset['Title'] = dataset['Title'].replace(['Lady', 'Countess','Capt', 'Col','Don', 'Dr', 'Major', 'Rev', 'Sir', 'Jonkheer', 'Dona'], 'Rare')

    dataset['Title'] = dataset['Title'].replace('Mlle', 'Miss')
    dataset['Title'] = dataset['Title'].replace('Ms', 'Miss')
    dataset['Title'] = dataset['Title'].replace('Mme', 'Mrs')

In [79]:
for dt in combine:
    dt["Embarked"]=dt["Embarked"].replace(to_replace=['C','Q','S'],value=[1,2,3])
    dt['Embarked'].fillna('S', inplace=True) ## using mode
    
    dt.Sex = dt['Sex'].replace(to_replace =["male","female"], value = [0,1])
    
    print(dt.head())
    

   Survived  Pclass  Sex   Age  SibSp  Parch     Fare  Embarked  Title
0         0       3    0  22.0      1      0   7.2500       3.0      1
1         1       1    1  38.0      1      0  71.2833       1.0      3
2         1       3    1  26.0      0      0   7.9250       3.0      2
3         1       1    1  35.0      1      0  53.1000       3.0      3
4         0       3    0  35.0      0      0   8.0500       3.0      1
   Pclass  Sex   Age  SibSp  Parch     Fare  Embarked  Title
0       3    0  34.5      0      0   7.8292         2      1
1       3    1  47.0      1      0   7.0000         3      3
2       2    0  62.0      0      0   9.6875         2      1
3       3    0  27.0      0      0   8.6625         3      1
4       3    1  22.0      1      1  12.2875         3      3


In [60]:

df_trn=df_trn.drop(['Name'],1)
df_tst=df_tst.drop(['Name'],1)
combine = [df_trn,df_tst]

In [61]:
df_trn

Survived  Pclass  Sex   Age  SibSp  Parch     Fare Embarked Title
0           0       3    0  22.0      1      0   7.2500      3.0    Mr
1           1       1    1  38.0      1      0  71.2833      1.0   Mrs
2           1       3    1  26.0      0      0   7.9250      3.0  Miss
3           1       1    1  35.0      1      0  53.1000      3.0   Mrs
4           0       3    0  35.0      0      0   8.0500      3.0    Mr
..        ...     ...  ...   ...    ...    ...      ...      ...   ...
886         0       2    0  27.0      0      0  13.0000      3.0  Rare
887         1       1    1  19.0      0      0  30.0000      3.0  Miss
888         0       3    1   NaN      1      2  23.4500      3.0  Miss
889         1       1    0  26.0      0      0  30.0000      1.0    Mr
890         0       3    0  32.0      0      0   7.7500      2.0    Mr

[891 rows x 9 columns]

In [62]:
title_mapping = {"Mr": 1, "Miss": 2, "Mrs": 3, "Master": 4, "Rare": 5}
for dataset in combine:
    dataset['Title'] = dataset['Title'].map(title_mapping)
    dataset['Title'] = dataset['Title'].fillna(0)

In [68]:
for df in combine:
    df['Age'].fillna(30.272590, inplace=True)
    df['Fare'].fillna(33, inplace=True)
    

## Model Inputs

In [69]:
X_train = df_trn.drop("Survived", axis=1)
Y_train = df_trn["Survived"]
X_test  = df_tst.copy()
X_train.shape, Y_train.shape, X_test.shape

((891, 8), (891,), (418, 8))

In [70]:
df_tst.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Pclass    418 non-null    int64  
 1   Sex       418 non-null    int64  
 2   Age       418 non-null    float64
 3   SibSp     418 non-null    int64  
 4   Parch     418 non-null    int64  
 5   Fare      418 non-null    float64
 6   Embarked  418 non-null    int64  
 7   Title     418 non-null    int64  
dtypes: float64(2), int64(6)
memory usage: 26.2 KB


In [82]:
X_train["Embarked"]=X_train["Embarked"].replace(to_replace=['C','Q','S'],value=[1,2,3])

In [83]:
X_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Pclass    891 non-null    int64  
 1   Sex       891 non-null    int64  
 2   Age       891 non-null    float64
 3   SibSp     891 non-null    int64  
 4   Parch     891 non-null    int64  
 5   Fare      891 non-null    float64
 6   Embarked  891 non-null    float64
 7   Title     891 non-null    int64  
dtypes: float64(3), int64(5)
memory usage: 55.8 KB


## Decision tree

In [84]:
clf = DecisionTreeClassifier()

clf = clf.fit(X_train,Y_train)

In [85]:
from matplotlib import pyplot as plt
from sklearn import tree

feature_cols=list(X_train.columns)

fig = plt.figure(figsize=(200,200))
_ = tree.plot_tree(clf,filled=True, rounded=True,feature_names = feature_cols,class_names=['0','1'])

In [89]:
fig.savefig("decistion_tree.png")

In [88]:
Y_pred = clf.predict(X_test)
acc_decision_tree = round(clf.score(X_train, Y_train) * 100, 2)
acc_decision_tree

98.43

In [94]:
kf = KFold(n_splits=5, random_state=None)

acc=0
    
for train_index , test_index in kf.split(X_train):
    x , xt = X_train.iloc[train_index,:],X_train.iloc[test_index,:]
    y , yt = Y_train[train_index],Y_train[test_index]
    clf = clf.fit(x,y)
    y_pred2 = clf.predict(xt)
    
    acc = acc + metrics.accuracy_score(yt, y_pred2)
    
    print(metrics.accuracy_score(yt, y_pred2))
    
print("Average Accuracy:", acc/5)

0.7597765363128491
0.7528089887640449
0.8426966292134831
0.7584269662921348
0.7528089887640449
Average Accuracy: 0.7733036218693113


In [96]:
clf2 = RandomForestClassifier(max_depth=9, random_state=0)
acc=0

for train_index , test_index in kf.split(X_train):
    x , xt = X_train.iloc[train_index,:],X_train.iloc[test_index,:]
    y , yt = Y_train[train_index],Y_train[test_index]
    clf = clf2.fit(x,y)
    y_pred2 = clf.predict(xt)
    
    acc = acc + metrics.accuracy_score(yt, y_pred2)
    
    print(metrics.accuracy_score(yt, y_pred2))
    
print("Average Accuracy:", acc/5)

0.8268156424581006
0.8146067415730337
0.8707865168539326
0.7921348314606742
0.8426966292134831
Average Accuracy: 0.829408072311845
